# Caffe Input 层

In [1]:
from pathlib import Path
from tvm_book.config import env
# 设置 caffeprotobuf环境
env.set_caffeproto(Path(env.__file__).parents[3]/"tests/caffeproto")
# 设置tvm环境
env.set_tvm("/media/pc/data/board/arria10/lxw/tasks/tvm-test")

In [2]:
from pathlib import Path
from google.protobuf import text_format
import caffe_pb2 as pb2

temp_dir = Path(".temp")
temp_dir.mkdir(exist_ok=True)

## Caffe Input 层

In [3]:
text = """
name: "data"
type: "Input"
top: "data"
input_param {
shape: { dim: 1 dim: 1 dim: 120 dim: 120 }
}
""".strip()
pl = text_format.Merge(text, pb2.LayerParameter())
pl

name: "data"
type: "Input"
top: "data"
input_param {
  shape {
    dim: 1
    dim: 1
    dim: 120
    dim: 120
  }
}

将 caffe Input 算子转换为 Relax 算子

In [4]:
from tvm.relax.testing import nn
dtype = "float32"

shape = pl.input_param.shape
assert len(shape)==1 and len(pl.top)==1, "Input 类型仅仅支持单输入单输出"
shape = list(shape[0].dim)
x = nn.Placeholder(shape, dtype, pl.name)
x.show()

## Caffe 多输入

In [5]:
text = """
name: "多输入"
layer {
  name: "data1"
  type: "Input"
  top: "data1"
  input_param {
    shape: { dim: 1 dim: 1 dim: 120 dim: 240 }
  }
}

layer {
  name: "data2"
  type: "Input"
  top: "data2"
  input_param {
    shape: { dim: 1 dim: 3 dim: 32 dim: 64 }
  }
}
""".strip()
predict_net = text_format.Merge(text, pb2.NetParameter())

In [6]:
from tvm.relax.testing import nn
dtype = "float32"

for pl in predict_net.layer:
    shape = pl.input_param.shape
    assert len(shape)==1 and len(pl.top)==1, "Input 类型仅仅支持单输入单输出"
    shape = list(shape[0].dim)
    x = nn.Placeholder(shape, dtype, pl.name)
    x.show()